In [3]:
pip install fastapi uvicorn


Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install python-multipart

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [1]:
!pip install mediapipe
!pip install mtcnn
!pip install keras-FaceNet
import mediapipe
#importing the pickle file

import pickle
with open('mini2.pkl', 'rb') as f:
    model = pickle.load(f)
try:
    classes = model.classes_
    #print("Model was trained on the following classes:", classes)
except AttributeError:
    print("Model does not have a 'classes_' attribute.")
#!/usr/bin/env python
# -*- coding: utf-8 -*-
import csv
import copy
import argparse
import itertools
from collections import Counter
from collections import deque

import cv2 as cv
import numpy as np
import mediapipe as mp

from utils import CvFpsCalc
from model import KeyPointClassifier
from model import PointHistoryClassifier
import cv2 as cv
import os
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
os.environ['TF_CPP_MIN_LOG_LEVEL']='2'


from keras_facenet import FaceNet
from mtcnn.mtcnn import MTCNN
detector=MTCNN()
embedder=FaceNet()
### Multithreaded environment 
### Both face recognition and hand gesture recognition takes place at once.


import cv2
import time
import copy
import csv
import threading
import numpy as np
from collections import Counter, deque
import mediapipe as mp
from mtcnn import MTCNN

# Initialize face detector
face_detector = MTCNN()
threshold = 0.6
embedder=FaceNet()
# Initialize hand detector
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(static_image_mode=False, max_num_hands=1, min_detection_confidence=0.5, min_tracking_confidence=0.5)

# Placeholder functions for face embedding and prediction
def pre_process_landmark(landmark_list):
    temp_landmark_list = [[lm[0], lm[1]] for lm in landmark_list]  # Convert tuples to lists

    base_x, base_y = temp_landmark_list[0][0], temp_landmark_list[0][1]

    for index in range(len(temp_landmark_list)):
        temp_landmark_list[index] = [
            temp_landmark_list[index][0] - base_x,
            temp_landmark_list[index][1] - base_y
        ]

    # Convert to a one-dimensional list
    flatten_landmark_list = [coord for point in temp_landmark_list for coord in point]
    return flatten_landmark_list

def get_embedding(face_img):
    face_img = cv2.resize(face_img, (160, 160))
    face_img = np.expand_dims(face_img, axis=0)
    return embedder.embeddings(face_img)[0]

def predict_name(face_embedding, threshold):
    probabilities = model.predict_proba(face_embedding)[0]
    predicted_index = np.argmax(probabilities)
    if probabilities[predicted_index] >= threshold:
        return model.classes_[predicted_index], "{:.2f}".format(probabilities[predicted_index])
    return "UNKNOWN", "{:.2f}".format(probabilities[predicted_index])

# FPS Calculation Class
class CvFpsCalc:
    def __init__(self, buffer_len=10):
        self.times = deque(maxlen=buffer_len)
    
    def get(self):
        self.times.append(time.time())
        if len(self.times) < 2:
            return 0.0
        return len(self.times) / (self.times[-1] - self.times[0])

fps_calculator = CvFpsCalc()

# Face Recognition Function
def recognize_faces(frame):
    result = face_detector.detect_faces(frame)
    if result:
        for face in result:
            bounding_box = face['box']
            face_img = frame[bounding_box[1]:bounding_box[1] + bounding_box[3], bounding_box[0]:bounding_box[0] + bounding_box[2]]
            face_embedding = [get_embedding(face_img)]
            name, ratio = predict_name(face_embedding, threshold)
            color = (0, 255, 0) if name != "UNKNOWN" else (255, 0, 0)
            cv2.rectangle(frame, (bounding_box[0], bounding_box[1]), (bounding_box[0] + bounding_box[2], bounding_box[1] + bounding_box[3]), color, 2)
            cv2.putText(frame, f"{name}", (bounding_box[0], bounding_box[1] - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, color, 2)
    return frame

# Hand Gesture Recognition Function
def recognize_hand_gesture(frame):
    image = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    results = hands.process(image)
    gesture = "Unknown"
    if results.multi_hand_landmarks:
        for hand_landmarks in results.multi_hand_landmarks:
            mp.solutions.drawing_utils.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)
            gesture = classify_gesture(hand_landmarks)  # Modify with actual gesture classification function
    return frame, gesture

# Actual hand gesture classification function
def classify_gesture(hand_landmarks):
    with open('model/keypoint_classifier/keypoint_classifier_label.csv', encoding='utf-8-sig') as f:
        keypoint_classifier_labels = [row[0] for row in csv.reader(f)]
    keypoint_classifier = KeyPointClassifier()
    landmark_list = [(lm.x, lm.y, lm.z) for lm in hand_landmarks.landmark]
    pre_processed_landmark_list = pre_process_landmark(landmark_list)
    gesture_id = keypoint_classifier(pre_processed_landmark_list)
    return keypoint_classifier_labels[gesture_id] if gesture_id < len(keypoint_classifier_labels) else "Unknown"

# Threaded Function to Run Face and Hand Gesture Recognition Simultaneously
def process_frame():
    cap = cv2.VideoCapture(0)
    recognized_gesture = "Unknown"
    
    while True:
        ret, frame = cap.read()
        if not ret:
            print("Failed to capture image. Exiting...")
            break

        fps = fps_calculator.get()
        
        face_thread = threading.Thread(target=recognize_faces, args=(frame,))
        face_thread.start()
        face_thread.join()
        
        frame, recognized_gesture = recognize_hand_gesture(frame)
        
        cv2.putText(frame, f"FPS: {fps:.2f}", (10, 30), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2)
        cv2.putText(frame, f"Finger Gesture: {recognized_gesture}", (10, 60), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2)
        
        cv2.imshow('Hand Gesture Recognition', frame)
        if cv2.waitKey(10) & 0xFF == 27:
            break
    
    cap.release()
    cv2.destroyAllWindows()

# Run the process
process_frame()

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable

1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 58ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 65ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step


In [3]:
from fastapi import FastAPI, UploadFile, File
import cv2
import numpy as np
import nest_asyncio
import uvicorn
import io

nest_asyncio.apply()  # Allows FastAPI to run inside Jupyter

app = FastAPI()
@app.post("/process/")
async def process_image(file: UploadFile = File(...)):
    contents = await file.read()
    np_array = np.frombuffer(contents, np.uint8)
    frame = cv2.imdecode(np_array, cv2.IMREAD_COLOR)
    
    processed_frame = process_frame(frame)
    _, encoded_image = cv2.imencode(".jpg", processed_frame)
    
    return {"processed_image": encoded_image.tobytes()}

# Run FastAPI inside Jupyter
uvicorn.run(app, host="127.0.0.1", port=8000)


INFO:     Started server process [21268]
INFO:     Waiting for application startup.
INFO:     Application startup complete.
INFO:     Uvicorn running on http://127.0.0.1:8000 (Press CTRL+C to quit)


INFO:     127.0.0.1:58901 - "GET /process/ HTTP/1.1" 405 Method Not Allowed
INFO:     127.0.0.1:58901 - "GET / HTTP/1.1" 404 Not Found
INFO:     127.0.0.1:58904 - "GET / HTTP/1.1" 404 Not Found
INFO:     127.0.0.1:58903 - "GET / HTTP/1.1" 404 Not Found
INFO:     127.0.0.1:58954 - "GET /docs HTTP/1.1" 200 OK
INFO:     127.0.0.1:58954 - "GET /openapi.json HTTP/1.1" 200 OK
INFO:     127.0.0.1:58999 - "POST /process/ HTTP/1.1" 500 Internal Server Error


ERROR:    Exception in ASGI application
Traceback (most recent call last):
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\protocols\http\h11_impl.py", line 403, in run_asgi
    result = await app(  # type: ignore[func-returns-value]
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\middleware\proxy_headers.py", line 60, in __call__
    return await self.app(scope, receive, send)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\fastapi\applications.py", line 1054, in __call__
    await super().__call__(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\applications.py", line 112, in __call__
    await self.middleware_stack(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\middleware\errors.py", line 1

INFO:     127.0.0.1:59000 - "POST /process/ HTTP/1.1" 500 Internal Server Error


ERROR:    Exception in ASGI application
Traceback (most recent call last):
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\protocols\http\h11_impl.py", line 403, in run_asgi
    result = await app(  # type: ignore[func-returns-value]
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\middleware\proxy_headers.py", line 60, in __call__
    return await self.app(scope, receive, send)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\fastapi\applications.py", line 1054, in __call__
    await super().__call__(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\applications.py", line 112, in __call__
    await self.middleware_stack(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\middleware\errors.py", line 1

...

ERROR:    Exception in ASGI application
Traceback (most recent call last):
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\protocols\http\h11_impl.py", line 403, in run_asgi
    result = await app(  # type: ignore[func-returns-value]
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\middleware\proxy_headers.py", line 60, in __call__
    return await self.app(scope, receive, send)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\fastapi\applications.py", line 1054, in __call__
    await super().__call__(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\applications.py", line 112, in __call__
    await self.middleware_stack(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\middleware\errors.py", line 1

INFO:     127.0.0.1:60319 - "POST /process/ HTTP/1.1" 500 Internal Server Error


ERROR:    Exception in ASGI application
Traceback (most recent call last):
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\protocols\http\h11_impl.py", line 403, in run_asgi
    result = await app(  # type: ignore[func-returns-value]
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\middleware\proxy_headers.py", line 60, in __call__
    return await self.app(scope, receive, send)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\fastapi\applications.py", line 1054, in __call__
    await super().__call__(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\applications.py", line 112, in __call__
    await self.middleware_stack(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\middleware\errors.py", line 1

INFO:     127.0.0.1:60320 - "POST /process/ HTTP/1.1" 500 Internal Server Error


ERROR:    Exception in ASGI application
Traceback (most recent call last):
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\protocols\http\h11_impl.py", line 403, in run_asgi
    result = await app(  # type: ignore[func-returns-value]
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\uvicorn\middleware\proxy_headers.py", line 60, in __call__
    return await self.app(scope, receive, send)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\fastapi\applications.py", line 1054, in __call__
    await super().__call__(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\applications.py", line 112, in __call__
    await self.middleware_stack(scope, receive, send)
  File "C:\Users\Vikas\AppData\Roaming\Python\Python312\site-packages\starlette\middleware\errors.py", line 1